# 1917 영화 댓글 Preprocessing

In [1]:
import requests
from bs4 import BeautifulSoup
from selenium import webdriver

import math
import time

## Naver 영화 페이지의 '1917'영화 댓글 Crawling

In [2]:
# Chromedriver로 chrome browser 실행
path = '/Users/wolee-mac/WorkSpace/chromedriver'
browser = webdriver.Chrome( path )

# Naver 영화 페이지의 '1917'영화 페이지 이동
url = 'https://movie.naver.com/movie/bi/mi/basic.nhn?code=187321'
browser.get( url )

# 평점에 더보기 링크 클릭
view_more = browser.find_element_by_xpath( '//*[@id="content"]/div[1]/div[4]/div[5]/div[2]/div[1]/a' )
view_more.click()

browser.switch_to_frame( browser.find_element_by_id( 'pointAfterListIframe' ) )

/Users/wolee-mac/opt/anaconda3/envs/nlp/lib/python3.7/site-packages/ipykernel_launcher.py:13: DeprecationWarning: use driver.switch_to.frame instead
  del sys.path[0]


In [3]:
# 전체 댓글수에 따른 페이지 계산
html0 = browser.page_source
html1 = BeautifulSoup( html0, 'lxml' )
html2 = html1.find( 'div', { 'class': 'score_total' } ).find( 'strong' ).findChildren( 'em' )[ 0 ].getText()
total_comment = int( html2.replace(',', '') )
total_page = total_comment / 10

print( total_comment )
print( total_page )
print( math.trunc( total_page ) )

3096
309.6
309


In [4]:
movie_comments = []

for page in range( 0, math.trunc( total_page ) ): # 전체 페이지를 이동
    time.sleep( 1 ) #1초의 시간 delay
    html0 = browser.page_source #selenuim에서 현재 있는 browser의 페이지 소스 불러오기
    html1 = BeautifulSoup( html0, 'lxml') #bs4를 이용하여 html로 파싱하기
    html2 = html1.find( 'div', { 'class': 'ifr_area basic_ifr' } ) #댓글을 포함하고 있는 tag찾기
    review0 = html2.find( 'div', { 'class': 'score_result' } ).find_all( 'li' ) #각 댓글별로 list화
    
    for i in range( len( review0 ) ): #한페이지 내에서 모든 댓글을 수집하기 위한 반복문
        review = review0[ i ].find( 'div',{ 'class': 'score_reple' } ).find( 'span' ).text.strip() #댓글
        if review not in '관람객': # 불필요한 내용 삭제
            movie_comments.append( review + '\n' )
        
    #다음페이지로 넘어가기
    if page == 0:
        browser.find_elements_by_xpath('//*[@class = "paging"]/div/a')[10].click()
    else:
        browser.find_elements_by_xpath('//*[@class = "paging"]/div/a')[11].click()


In [119]:
print( movie_comments )

['충무로: 이거 어케하는거냐?\n', '촬영감독의 영혼까지 갈아넣은 마스터피스\n', '오스카 작품상 탔어도 할말 없었을것 같다.\n', '주인공을 카메라가 계속 따라가는데.. 세트장이 엄청 넓은거에 놀랐습니다. 직접 1차대전에 참전하는 느낌.. 이때당시 군인들 20년뒤 히틀러라는 극악의 악마로 자식들 다 전장에 몰리고 더 최악의 고통을 받을껀데 참.....\n', '닥터스트레인지의 판단력이 좋았다.\n', '솔직히 연출력만으로 최고의 영화다. 마치 우리가 투명인간이 되서 그들을 지켜보는 듯했다. 마지막장면은 영화 내내 쉴시간이 없었던것에 대한 피로감을 풀어줘서 기승전결도 완벽.\n', '아카데미 작품상이야 작품전체를 보는거니 기생충이 받을수도 있다고 보는데 감독상은 1917 줬어도 할말 없음. 감독의 참신성이 빛을 발함. 결론적으로 아카데미 작품상과 감독상을 1917이 받았어도 아무 할말 없는 것이...\n', '스포일러가 포함된 감상평입니다. 감상평 보기\n', '진짜 원테이크 장면 너무 긴거 아님?? 촬영하기 진짜 힘들었을 듯...\n', '솔직히 나는 기생충보다 이영화가 더 재미있었다.\n', '막판에 횡으로 수많은 병사가 신호와 함께 우르르 튀어나올때 주인공 혼자 종으로 막 달리는 장면 와 진짜ㅋㅋㅋㅋ대박 무조건 아이맥스로 보세요!\n', '원테이크 촬영신은 볼때마다 대단하다 후보에 오를만 했음\n', '스포일러가 포함된 감상평입니다. 감상평 보기\n', '일단..극장에서 보는걸  추천드립니다.카메라감독 상 줘야 할판  엄청나게  잘 찍음\n', '솔직히 샘 멘데스 감독 좀 억울할듯기생충도 재밌게 봤지만, 이거 보고나서 좀 억울했겠다는 생각이 팍듬..\n', '동료를 잃고 목숨을 잃을 위기를 극복해나가며 달려 얻은 것은 전쟁의 무의미함과 허무함 뿐.\n', '전쟁이 끝나는 길은 마지막 한사람까지 죽는 것이다.\n', '이 모든 것이 하루만의 일이라니...\n', '기생충이 그냥 백인이 나온 헐리우드 영화였다면 절대 1917을 이기지 못했을것. 191

In [176]:
# 파일 저장
with open( 'comment_1917.txt', 'w', encoding = 'utf-8' ) as f:
    for comment in movie_comments:
        f.write( comment + '\n' )

# 파일에서 load
movie_comments = []
with open( 'comment_1917.txt', 'r', encoding = 'utf-8' ) as f:
    lines = f.readlines()
    for line in lines:
        movie_comments.append( line.rstrip( '\n' ) )

print( movie_comments )

['충무로: 이거 어케하는거냐?', '', '촬영감독의 영혼까지 갈아넣은 마스터피스', '', '오스카 작품상 탔어도 할말 없었을것 같다.', '', '주인공을 카메라가 계속 따라가는데.. 세트장이 엄청 넓은거에 놀랐습니다. 직접 1차대전에 참전하는 느낌.. 이때당시 군인들 20년뒤 히틀러라는 극악의 악마로 자식들 다 전장에 몰리고 더 최악의 고통을 받을껀데 참.....', '', '닥터스트레인지의 판단력이 좋았다.', '', '솔직히 연출력만으로 최고의 영화다. 마치 우리가 투명인간이 되서 그들을 지켜보는 듯했다. 마지막장면은 영화 내내 쉴시간이 없었던것에 대한 피로감을 풀어줘서 기승전결도 완벽.', '', '아카데미 작품상이야 작품전체를 보는거니 기생충이 받을수도 있다고 보는데 감독상은 1917 줬어도 할말 없음. 감독의 참신성이 빛을 발함. 결론적으로 아카데미 작품상과 감독상을 1917이 받았어도 아무 할말 없는 것이...', '', '스포일러가 포함된 감상평입니다. 감상평 보기', '', '진짜 원테이크 장면 너무 긴거 아님?? 촬영하기 진짜 힘들었을 듯...', '', '솔직히 나는 기생충보다 이영화가 더 재미있었다.', '', '막판에 횡으로 수많은 병사가 신호와 함께 우르르 튀어나올때 주인공 혼자 종으로 막 달리는 장면 와 진짜ㅋㅋㅋㅋ대박 무조건 아이맥스로 보세요!', '', '원테이크 촬영신은 볼때마다 대단하다 후보에 오를만 했음', '', '스포일러가 포함된 감상평입니다. 감상평 보기', '', '일단..극장에서 보는걸  추천드립니다.카메라감독 상 줘야 할판  엄청나게  잘 찍음', '', '솔직히 샘 멘데스 감독 좀 억울할듯기생충도 재밌게 봤지만, 이거 보고나서 좀 억울했겠다는 생각이 팍듬..', '', '동료를 잃고 목숨을 잃을 위기를 극복해나가며 달려 얻은 것은 전쟁의 무의미함과 허무함 뿐.', '', '전쟁이 끝나는 길은 마지막 한사람까지 죽는 것이다.', '', '이 모든 것이 하루만의 일이라니...', '', '기생충이 그냥 백인이 

In [177]:
# 문자열로 변환
movie_comment = ''
for comment in movie_comments:
    movie_comment += comment
print( movie_comment )

충무로: 이거 어케하는거냐?촬영감독의 영혼까지 갈아넣은 마스터피스오스카 작품상 탔어도 할말 없었을것 같다.주인공을 카메라가 계속 따라가는데.. 세트장이 엄청 넓은거에 놀랐습니다. 직접 1차대전에 참전하는 느낌.. 이때당시 군인들 20년뒤 히틀러라는 극악의 악마로 자식들 다 전장에 몰리고 더 최악의 고통을 받을껀데 참.....닥터스트레인지의 판단력이 좋았다.솔직히 연출력만으로 최고의 영화다. 마치 우리가 투명인간이 되서 그들을 지켜보는 듯했다. 마지막장면은 영화 내내 쉴시간이 없었던것에 대한 피로감을 풀어줘서 기승전결도 완벽.아카데미 작품상이야 작품전체를 보는거니 기생충이 받을수도 있다고 보는데 감독상은 1917 줬어도 할말 없음. 감독의 참신성이 빛을 발함. 결론적으로 아카데미 작품상과 감독상을 1917이 받았어도 아무 할말 없는 것이...스포일러가 포함된 감상평입니다. 감상평 보기진짜 원테이크 장면 너무 긴거 아님?? 촬영하기 진짜 힘들었을 듯...솔직히 나는 기생충보다 이영화가 더 재미있었다.막판에 횡으로 수많은 병사가 신호와 함께 우르르 튀어나올때 주인공 혼자 종으로 막 달리는 장면 와 진짜ㅋㅋㅋㅋ대박 무조건 아이맥스로 보세요!원테이크 촬영신은 볼때마다 대단하다 후보에 오를만 했음스포일러가 포함된 감상평입니다. 감상평 보기일단..극장에서 보는걸  추천드립니다.카메라감독 상 줘야 할판  엄청나게  잘 찍음솔직히 샘 멘데스 감독 좀 억울할듯기생충도 재밌게 봤지만, 이거 보고나서 좀 억울했겠다는 생각이 팍듬..동료를 잃고 목숨을 잃을 위기를 극복해나가며 달려 얻은 것은 전쟁의 무의미함과 허무함 뿐.전쟁이 끝나는 길은 마지막 한사람까지 죽는 것이다.이 모든 것이 하루만의 일이라니...기생충이 그냥 백인이 나온 헐리우드 영화였다면 절대 1917을 이기지 못했을것. 1917은 오히려 백인의 헐리우드 영화라 차별받음. 진짜 근래 보기 드믄 명작스포일러가 포함된 감상평입니다. 감상평 보기전쟁씬 안나온다고 보지말라던 사람들 너무 한심하다병사를 따라가다보면 경험할 전쟁의 

### 특수문제 제거

In [178]:
r = '[-=+,#/\?:^$.@*\"※~&%ㆍ!』\\‘|\(\)\[\]\<\>`\'…》]'
movie_comment = re.sub( r, '', movie_comment )
print( movie_comment )

충무로 이거 어케하는거냐촬영감독의 영혼까지 갈아넣은 마스터피스오스카 작품상 탔어도 할말 없었을것 같다주인공을 카메라가 계속 따라가는데 세트장이 엄청 넓은거에 놀랐습니다 직접 1차대전에 참전하는 느낌 이때당시 군인들 20년뒤 히틀러라는 극악의 악마로 자식들 다 전장에 몰리고 더 최악의 고통을 받을껀데 참닥터스트레인지의 판단력이 좋았다솔직히 연출력만으로 최고의 영화다 마치 우리가 투명인간이 되서 그들을 지켜보는 듯했다 마지막장면은 영화 내내 쉴시간이 없었던것에 대한 피로감을 풀어줘서 기승전결도 완벽아카데미 작품상이야 작품전체를 보는거니 기생충이 받을수도 있다고 보는데 감독상은 1917 줬어도 할말 없음 감독의 참신성이 빛을 발함 결론적으로 아카데미 작품상과 감독상을 1917이 받았어도 아무 할말 없는 것이스포일러가 포함된 감상평입니다 감상평 보기진짜 원테이크 장면 너무 긴거 아님 촬영하기 진짜 힘들었을 듯솔직히 나는 기생충보다 이영화가 더 재미있었다막판에 횡으로 수많은 병사가 신호와 함께 우르르 튀어나올때 주인공 혼자 종으로 막 달리는 장면 와 진짜ㅋㅋㅋㅋ대박 무조건 아이맥스로 보세요원테이크 촬영신은 볼때마다 대단하다 후보에 오를만 했음스포일러가 포함된 감상평입니다 감상평 보기일단극장에서 보는걸  추천드립니다카메라감독 상 줘야 할판  엄청나게  잘 찍음솔직히 샘 멘데스 감독 좀 억울할듯기생충도 재밌게 봤지만 이거 보고나서 좀 억울했겠다는 생각이 팍듬동료를 잃고 목숨을 잃을 위기를 극복해나가며 달려 얻은 것은 전쟁의 무의미함과 허무함 뿐전쟁이 끝나는 길은 마지막 한사람까지 죽는 것이다이 모든 것이 하루만의 일이라니기생충이 그냥 백인이 나온 헐리우드 영화였다면 절대 1917을 이기지 못했을것 1917은 오히려 백인의 헐리우드 영화라 차별받음 진짜 근래 보기 드믄 명작스포일러가 포함된 감상평입니다 감상평 보기전쟁씬 안나온다고 보지말라던 사람들 너무 한심하다병사를 따라가다보면 경험할 전쟁의 참상과 자연스레 따라오는 두려움과 먹먹함 이건 판타지를 제외한 영화의 기술이 구현

## Text Proprocessing

### 형태소 분석

In [123]:
from nltk.tokenize import word_tokenize
from konlpy.tag import Okt
import re

In [124]:
okt = Okt()

### 형태소 추출

In [125]:
morphemes = []
for morphs in okt.morphs( movie_comment ):
    morphemes.append( morphs )
print( morphemes )

['충무로', '이', '거', '어케', '하는거냐', '촬영감독', '의', '영혼', '까지', '갈아', '넣은', '마스터피스', '오스카', '작품', '상', '탔어도', '할말', '없었을것', '같다', '주인공', '을', '카메라', '가', '계속', '따라가는데', '세트', '장이', '엄청', '넓은거에', '놀랐습니다', '직접', '1', '차', '대전', '에', '참전', '하는', '느낌', '이', '때', '당시', '군', '인들', '20년', '뒤', '히틀러', '라는', '극악', '의', '악마', '로', '자식', '들', '다', '전장', '에', '몰리', '고', '더', '최악', '의', '고통', '을', '받을껀데', '참', '닥터스', '트레인', '지', '의', '판단력', '이', '좋았다', '솔직히', '연출', '력', '만으로', '최고', '의', '영화', '다', '마치', '우리', '가', '투명인간', '이', '되서', '그', '들', '을', '지켜보는', '듯', '했다', '마지막', '장면', '은', '영화', '내내', '쉴', '시간', '이', '없었던것에', '대한', '피로', '감', '을', '풀어줘서', '기승', '전결', '도', '완벽', '아카데미', '작품', '상', '이야', '작품', '전체', '를', '보는거니', '기생충', '이', '받을수도', '있다고', '보는데', '감독', '상', '은', '1917', '줬어도', '할말', '없음', '감독', '의', '참신', '성', '이', '빛', '을', '발함', '결론', '적', '으로', '아카데미', '작품', '상과', '감독', '상', '을', '1917', '이', '받았어도', '아무', '할말', '없는', '것', '이', '스포일러', '가', '포함', '된', '감상', '평', '입니다', '감상', '평', '보기', '진짜', '

### 형태소 추출 및 어간 추출

In [126]:
morphemes = []
for morphs in okt.morphs( movie_comment, stem = True ):
    morphemes.append( morphs )
print( morphemes )

['충무로', '이', '거', '어케', '하다', '촬영감독', '의', '영혼', '까지', '갈아', '넣다', '마스터피스', '오스카', '작품', '상', '타다', '하다', '없다', '같다', '주인공', '을', '카메라', '가', '계속', '따라가다', '세트', '장이', '엄청', '넓다', '놀라다', '직접', '1', '차', '대전', '에', '참전', '하다', '느낌', '이', '때', '당시', '군', '인들', '20년', '뒤', '히틀러', '라는', '극악', '의', '악마', '로', '자식', '들', '다', '전장', '에', '몰리', '고', '더', '최악', '의', '고통', '을', '받을껀데', '차다', '닥터스', '트레인', '지', '의', '판단력', '이', '좋다', '솔직하다', '연출', '력', '만으로', '최고', '의', '영화', '다', '마치', '우리', '가', '투명인간', '이', '되다', '그', '들', '을', '지켜보다', '듯', '하다', '마지막', '장면', '은', '영화', '내내', '쉬다', '시간', '이', '없다', '대한', '피로', '감', '을', '풀다', '기승', '전결', '도', '완벽', '아카데미', '작품', '상', '이야', '작품', '전체', '를', '보다', '기생충', '이', '받다', '있다', '보다', '감독', '상', '은', '1917', '주다', '하다', '없다', '감독', '의', '참신', '성', '이', '빛', '을', '발함', '결론', '적', '으로', '아카데미', '작품', '상과', '감독', '상', '을', '1917', '이', '받다', '아무', '하다', '없다', '것', '이', '스포일러', '가', '포함', '되다', '감상', '평', '이다', '감상', '평', '보기', '진짜', '원', '테이크', '장면', '너무',

### 행태소 추출 및 정규화 

In [127]:
morphemes = []
for morphs in okt.morphs( movie_comment, norm = True ):
    morphemes.append( morphs )
print( morphemes )

['충무로', '이', '거', '어떻게', '하는거냐', '촬영감독', '의', '영혼', '까지', '갈아', '넣은', '마스터피스', '오스카', '작품', '상', '탔어도', '할말', '없었을것', '같다', '주인공', '을', '카메라', '가', '계속', '따라가는데', '세트', '장이', '엄청', '넓은거에', '놀랐습니다', '직접', '1', '차', '대전', '에', '참전', '하는', '느낌', '이', '때', '당시', '군', '인들', '20년', '뒤', '히틀러', '라는', '극악', '의', '악마', '로', '자식', '들', '다', '전장', '에', '몰리', '고', '더', '최악', '의', '고통', '을', '받을껀데', '참', '닥터스', '트레인', '지', '의', '판단력', '이', '좋았다', '솔직히', '연출', '력', '만으로', '최고', '의', '영화', '다', '마치', '우리', '가', '투명인간', '이', '되서', '그', '들', '을', '지켜보는', '듯', '했다', '마지막', '장면', '은', '영화', '내내', '쉴', '시간', '이', '없었던것에', '대한', '피로', '감', '을', '풀어줘서', '기승', '전결', '도', '완벽', '아카데미', '작품', '상', '이야', '작품', '전체', '를', '보는거니', '기생충', '이', '받을수도', '있다고', '보는데', '감독', '상', '은', '1917', '줬어도', '할말', '없음', '감독', '의', '참신', '성', '이', '빛', '을', '발함', '결론', '적', '으로', '아카데미', '작품', '상과', '감독', '상', '을', '1917', '이', '받았어도', '아무', '할말', '없는', '것', '이', '스포일러', '가', '포함', '된', '감상', '평', '입니다', '감상', '평', '보기', '진짜', 

### 명사 분리

In [128]:
morphemes = []
for morphs in okt.nouns( movie_comment ):
    morphemes.append( morphs )
print( morphemes )

['충무로', '거', '어케', '촬영감독', '영혼', '마스터피스', '오스카', '작품', '주인공', '카메라', '계속', '세트', '직접', '차', '대전', '참전', '느낌', '때', '당시', '군', '히틀러', '극악', '악마', '자식', '전장', '몰리', '더', '최악', '고통', '받을껀데', '닥터스', '트레인', '의', '판단력', '연출', '최고', '영화', '마치', '우리', '투명인간', '그', '듯', '마지막', '장면', '영화', '내내', '시간', '대한', '피로', '감', '기승', '전결', '완벽', '아카데미', '작품', '작품', '전체', '기생충', '감독', '감독', '참신', '빛', '발함', '결론', '아카데미', '작품', '상과', '감독', '이', '아무', '것', '스포일러', '포함', '감상', '평', '감상', '평', '보기', '진짜', '테이크', '장면', '촬영', '진짜', '듯', '나', '기생충', '이영화', '더', '막판', '횡', '병사', '신호', '우르르', '때', '주인공', '혼자', '종', '막', '장면', '진짜', '대박', '무조건', '아이맥스', '요원', '테이크', '촬영', '볼때', '후보', '스포일러', '포함', '감상', '평', '감상', '평', '보기', '일단', '극장', '추천', '카메라감독', '상', '판', '샘', '데스', '감독', '좀', '기생충', '거', '좀', '생각', '팍듬동료', '목숨', '위기', '극복', '것', '전쟁', '뿐', '전쟁', '마지막', '사람', '것', '모든', '것', '하루', '일이', '기생충', '그냥', '백인', '헐리우드', '영화', '절대', '이기', '은', '오히려', '백인', '헐리우드', '영화', '차별', '진짜', '근래', '보기', '드믄', '명작', '스포일러', '포함'

### 어절 분리

In [129]:
morphemes = []
for morphs in okt.phrases( movie_comment ):
    morphemes.append( morphs )
print( morphemes )

['충무로', '충무로 이거', '충무로 이거 어케', '촬영감독', '촬영감독의 영혼', '마스터피스오스카', '마스터피스오스카 작품상', '주인공', '카메라', '계속', '세트장이', '직접', '직접 1차대전', '참전', '참전하는 느낌', '참전하는 느낌 이때당시', '참전하는 느낌 이때당시 군', '20년', '히틀러', '극악', '극악의 악마', '자식들', '전장', '몰리', '더 최악', '더 최악의 고통', '받을껀데', '닥터스트레인', '의 판단력', '연출력', '최고', '최고의 영화', '마치', '마치 우리', '투명인간', '그들', '마지막장면', '영화', '영화 내내', '영화 내내 쉴시간', '대한', '대한 피로감', '기승전결', '완벽아카데미', '완벽아카데미 작품상', '작품전체', '기생충', '감독상', '1917', '감독', '감독의 참신성', '발함', '아카데미', '아카데미 작품상과', '아카데미 작품상과 감독상', '1917이', '아무', '아무 할말 없는 것이스포일러', '포함', '포함된 감상평', '감상평', '감상평 보기진짜', '감상평 보기진짜 원테이크', '감상평 보기진짜 원테이크 장면', '촬영', '진짜', '진짜 힘들었을 듯', '이영화', '막판', '수많은 병사', '신호', '우르르', '우르르 튀어나올때', '우르르 튀어나올때 주인공', '우르르 튀어나올때 주인공 혼자', '우르르 튀어나올때 주인공 혼자 종', '막 달리는 장면', '대박', '대박 무조건', '대박 무조건 아이맥스', '요원테이크', '요원테이크 촬영', '요원테이크 촬영신은 볼때', '후보', '스포일러', '감상평 보기일단극장', '추천', '카메라감독', '카메라감독 상', '샘 멘데스', '샘 멘데스 감독', '샘 멘데스 감독 좀', '이거', '좀 억울했겠다는 생각', '팍듬동료', '목숨', '위기', '극복', '전쟁', '뿐전쟁', '길은 마지막', '길은 마지막 한사람', '이 모든',

### 품사 태깅

In [130]:
morphemes = []
for morphs in okt.pos( movie_comment, join = True ):
    morphemes.append( morphs )
print( morphemes )

['충무로/Noun', '이/Determiner', '거/Noun', '어케/Noun', '하는거냐/Verb', '촬영감독/Noun', '의/Josa', '영혼/Noun', '까지/Josa', '갈아/Adverb', '넣은/Verb', '마스터피스/Noun', '오스카/Noun', '작품/Noun', '상/Suffix', '탔어도/Verb', '할말/Verb', '없었을것/Adjective', '같다/Adjective', '주인공/Noun', '을/Josa', '카메라/Noun', '가/Josa', '계속/Noun', '따라가는데/Verb', '세트/Noun', '장이/Suffix', '엄청/Adverb', '넓은거에/Adjective', '놀랐습니다/Verb', '직접/Noun', '1/Number', '차/Noun', '대전/Noun', '에/Josa', '참전/Noun', '하는/Verb', '느낌/Noun', '이/Determiner', '때/Noun', '당시/Noun', '군/Noun', '인들/Josa', '20년/Number', '뒤/Foreign', '히틀러/Noun', '라는/Josa', '극악/Noun', '의/Josa', '악마/Noun', '로/Josa', '자식/Noun', '들/Suffix', '다/Adverb', '전장/Noun', '에/Josa', '몰리/Noun', '고/Josa', '더/Noun', '최악/Noun', '의/Josa', '고통/Noun', '을/Josa', '받을껀데/Noun', '참/Verb', '닥터스/Noun', '트레인/Noun', '지/Josa', '의/Noun', '판단력/Noun', '이/Josa', '좋았다/Adjective', '솔직히/Adjective', '연출/Noun', '력/Suffix', '만으로/Josa', '최고/Noun', '의/Josa', '영화/Noun', '다/Josa', '마치/Noun', '우리/Noun', '가/Josa', '투명인간/Noun', '이/Josa', '되서

### 불용어 Load

In [131]:
stop_words = []
with open( 'stopwords.txt', 'r', encoding = 'utf-8' ) as f:
    lines = f.readlines()
    for line in lines:
        stop_words.append( line.rstrip( '\n' ) )

print( stop_words )

['아', '휴', '아이구', '아이쿠', '아이고', '어', '나', '우리', '저희', '따라', '의해', '을', '를', '에', '의', '가', '으로', '로', '에게', '뿐이다', '의거하여', '근거하여', '입각하여', '기준으로', '예하면', '예를 들면', '예를 들자면', '저', '소인', '소생', '저희', '지말고', '하지마', '하지마라', '다른', '물론', '또한', '그리고', '비길수 없다', '해서는 안된다', '뿐만 아니라', '만이 아니다', '만은 아니다', '막론하고', '관계없이', '그치지 않다', '그러나', '그런데', '하지만', '든간에', '논하지 않다', '따지지 않다', '설사', '비록', '더라도', '아니면', '만 못하다', '하는 편이 낫다', '불문하고', '향하여', '향해서', '향하다', '쪽으로', '틈타', '이용하여', '타다', '오르다', '제외하고', '이 외에', '이 밖에', '하여야', '비로소', '한다면 몰라도', '외에도', '이곳', '여기', '부터', '기점으로', '따라서', '할 생각이다', '하려고하다', '이리하여', '그리하여', '그렇게 함으로써', '하지만', '일때', '할때', '앞에서', '중에서', '보는데서', '으로써', '로써', '까지', '해야한다', '일것이다', '반드시', '할줄알다', '할수있다', '할수있어', '임에 틀림없다', '한다면', '등', '등등', '제', '겨우', '단지', '다만', '할뿐', '딩동', '댕그', '대해서', '대하여', '대하면', '훨씬', '얼마나', '얼마만큼', '얼마큼', '남짓', '여', '얼마간', '약간', '다소', '좀', '조금', '다수', '몇', '얼마', '지만', '하물며', '또한', '그러나', '그렇지만', '하지만', '이외에도', '대해 말하자면', '뿐이다', '다음에', '반대로', '반대로 말하자면', '이와 반대로',

### 불용어 제거

In [162]:
results = []
for word in okt.morphs( movie_comment ):
    if word not in stop_words:
        results.append( word )
print( results )

['충무로', '거', '어케', '하는거냐', '촬영감독', '영혼', '갈아', '넣은', '마스터피스', '오스카', '작품', '상', '탔어도', '할말', '없었을것', '주인공', '카메라', '계속', '따라가는데', '세트', '장이', '엄청', '넓은거에', '놀랐습니다', '직접', '1', '차', '대전', '참전', '하는', '느낌', '당시', '군', '인들', '20년', '뒤', '히틀러', '라는', '극악', '악마', '자식', '다', '전장', '몰리', '고', '더', '최악', '고통', '받을껀데', '닥터스', '트레인', '지', '판단력', '좋았다', '솔직히', '연출', '력', '만으로', '최고', '영화', '다', '투명인간', '되서', '지켜보는', '듯', '했다', '마지막', '장면', '은', '영화', '내내', '쉴', '없었던것에', '대한', '피로', '감', '풀어줘서', '기승', '전결', '도', '완벽', '아카데미', '작품', '상', '이야', '작품', '전체', '보는거니', '기생충', '받을수도', '있다고', '보는데', '감독', '상', '은', '1917', '줬어도', '할말', '없음', '감독', '참신', '성', '빛', '발함', '결론', '적', '아카데미', '작품', '상과', '감독', '상', '1917', '받았어도', '아무', '할말', '없는', '스포일러', '포함', '된', '감상', '평', '입니다', '감상', '평', '보기', '진짜', '원', '테이크', '장면', '너무', '긴거', '아님', '촬영', '하기', '진짜', '힘들었을', '듯', '솔직히', '는', '기생충', '보다', '이영화', '더', '재미있었다', '막판', '횡', '수많은', '병사', '신호', '튀어나올', '주인공', '종', '막', '달리는', '장면', '진짜', 'ㅋㅋㅋㅋ', '대박', '무조건',

### Integer Encoding

In [133]:
from tensorflow.keras.preprocessing.text import Tokenizer

In [169]:
tokenizer = Tokenizer()
tokenizer.fit_on_texts( results )

In [170]:
print( tokenizer.word_index )

{'영화': 1, '은': 2, '전쟁': 3, '는': 4, '한': 5, '테이크': 6, '도': 7, '촬영': 8, '연출': 9, '평': 10, '감상': 11, '진짜': 12, '적': 13, '전쟁영화': 14, '스토리': 15, '입니다': 16, '몰입': 17, '다': 18, '롱': 19, '정말': 20, '기생충': 21, '작품': 22, '최고': 23, '상': 24, '너무': 25, '기법': 26, '된': 27, '감': 28, '만': 29, '느낌': 30, '보기': 31, '수': 32, '잘': 33, '주인공': 34, '하는': 35, '원': 36, '포함': 37, '감동': 38, '스포일러': 39, '꼭': 40, '인': 41, '1': 42, '내': 43, '하고': 44, '이다': 45, '게': 46, '생각': 47, '안': 48, '장면': 49, '못': 50, '1917': 51, '연기': 52, '긴장감': 53, '속': 54, '처음': 55, '있는': 56, '영화관': 57, '말': 58, '중': 59, '본': 60, '상미': 61, '더': 62, '점': 63, '감독': 64, '할': 65, '없는': 66, '보는': 67, '사람': 68, '카메라': 69, '보다': 70, '아이맥스': 71, '정도': 72, '그냥': 73, '차': 74, '영상': 75, '내내': 76, '아카데미': 77, '극장': 78, '듯': 79, '끝': 80, '고': 81, '보고': 82, '볼': 83, '마지막': 84, '같은': 85, '인생': 86, '명작': 87, '배우': 88, '해서': 89, '평점': 90, '보세요': 91, '터': 92, '거': 93, '걸': 94, '중간': 95, '모든': 96, '코로나': 97, '현장': 98, '했다': 99, '없다': 100, '덩케르크': 101, '함': 102, 

In [171]:
print( tokenizer.word_counts )

OrderedDict([('충무로', 2), ('거', 52), ('어케', 10), ('하는거냐', 1), ('촬영감독', 13), ('영혼', 5), ('갈아', 5), ('넣은', 2), ('마스터피스', 10), ('오스카', 33), ('작품', 172), ('상', 160), ('탔어도', 4), ('할말', 10), ('없었을것', 1), ('주인공', 124), ('카메라', 75), ('계속', 36), ('따라가는데', 1), ('세트', 16), ('장이', 3), ('엄청', 27), ('넓은거에', 1), ('놀랐습니다', 2), ('직접', 16), ('1', 107), ('차', 72), ('대전', 33), ('참전', 10), ('하는', 119), ('느낌', 131), ('당시', 6), ('군', 5), ('인들', 1), ('20년', 1), ('뒤', 12), ('히틀러', 1), ('라는', 34), ('극악', 1), ('악마', 1), ('자식', 1), ('다', 180), ('전장', 43), ('몰리', 1), ('고', 66), ('더', 80), ('최악', 9), ('고통', 8), ('받을껀데', 1), ('닥터스', 4), ('트레인', 4), ('지', 45), ('판단력', 1), ('좋았다', 13), ('솔직히', 31), ('연출', 253), ('력', 44), ('만으로', 7), ('최고', 168), ('영화', 1088), ('투명인간', 1), ('되서', 5), ('지켜보는', 3), ('듯', 68), ('했다', 50), ('마지막', 64), ('장면', 96), ('은', 399), ('내내', 70), ('쉴', 2), ('없었던것에', 1), ('대한', 15), ('피로', 4), ('감', 134), ('풀어줘서', 1), ('기승', 2), ('전결', 2), ('도', 258), ('완벽', 7), ('아카데미', 69), ('이야', 11), ('전체', 14)

In [166]:
vocab_size = 50
tokenizer = Tokenizer()
tokenizer.fit_on_texts( results )

In [167]:
vocab_size = 50
words_frequency = [ w for w, c in tokenizer.word_index.items() if c >= vocab_size + 1 ] # 인덱스가 50 초과인 단어 제거
for w in words_frequency:
    del tokenizer.word_index[ w ] # 해당 단어에 대한 인덱스 정보를 삭제
    del tokenizer.word_counts[ w ] # 해당 단어에 대한 카운트 정보를 삭제
print( tokenizer.word_index )
print()
print( tokenizer.word_counts )
print()
print( tokenizer.texts_to_sequences( results ) )

{'영화': 1, '은': 2, '전쟁': 3, '는': 4, '한': 5, '테이크': 6, '도': 7, '촬영': 8, '연출': 9, '평': 10, '감상': 11, '진짜': 12, '적': 13, '전쟁영화': 14, '스토리': 15, '입니다': 16, '몰입': 17, '다': 18, '롱': 19, '정말': 20, '기생충': 21, '작품': 22, '최고': 23, '상': 24, '너무': 25, '기법': 26, '된': 27, '감': 28, '만': 29, '느낌': 30, '보기': 31, '수': 32, '잘': 33, '주인공': 34, '하는': 35, '원': 36, '포함': 37, '감동': 38, '스포일러': 39, '꼭': 40, '인': 41, '1': 42, '내': 43, '하고': 44, '이다': 45, '게': 46, '생각': 47, '안': 48, '장면': 49, '못': 50}

OrderedDict([('작품', 172), ('상', 160), ('주인공', 124), ('1', 107), ('하는', 119), ('느낌', 131), ('다', 180), ('연출', 253), ('최고', 168), ('영화', 1088), ('장면', 96), ('은', 399), ('감', 134), ('도', 258), ('기생충', 173), ('적', 206), ('스포일러', 112), ('포함', 113), ('된', 139), ('감상', 237), ('평', 242), ('입니다', 190), ('보기', 127), ('진짜', 210), ('원', 119), ('테이크', 296), ('너무', 150), ('촬영', 257), ('는', 377), ('잘', 126), ('생각', 104), ('전쟁', 378), ('한', 331), ('이다', 105), ('못', 93), ('안', 100), ('수', 127), ('롱', 179), ('인', 108), ('기법', 141), 

In [179]:
vocab_size = 50
tokenizer = Tokenizer( num_words = vocab_size + 2, oov_token = 'OOV' ) 
# 빈도수 상위 50개 단어만 사용, 숫자 0과 OOV를 고려해서 단어 집합의 크기는 +2
tokenizer.fit_on_texts( results )

print( tokenizer.texts_to_sequences( results ) )

[[1], [1], [1], [1], [1], [1], [1], [1], [1], [1], [23], [25], [1], [1], [1], [35], [1], [1], [1], [1], [1], [1], [1], [1], [1], [43], [1], [1], [1], [36], [31], [1], [1], [1], [1], [1], [1], [1], [1], [1], [1], [19], [1], [1], [1], [1], [1], [1], [1], [1], [1], [1], [1], [1], [1], [10], [1], [1], [24], [2], [19], [1], [1], [1], [1], [1], [1], [50], [3], [2], [1], [1], [1], [1], [1], [29], [1], [1], [1], [8], [1], [1], [23], [25], [1], [23], [1], [1], [22], [1], [1], [1], [1], [25], [3], [1], [1], [1], [1], [1], [1], [1], [1], [1], [1], [14], [1], [23], [1], [1], [25], [1], [1], [1], [1], [1], [40], [38], [28], [12], [11], [17], [12], [11], [32], [13], [37], [7], [50], [26], [1], [1], [9], [1], [13], [1], [1], [1], [5], [22], [1], [1], [1], [1], [1], [1], [1], [1], [1], [1], [35], [1], [1], [1], [50], [13], [1], [1], [1], [1], [1], [1], [7], [9], [1], [1], [1], [1], [1], [1], [1], [40], [38], [28], [12], [11], [17], [12], [11], [32], [1], [1], [1], [1], [1], [25], [1], [1], [1], [1], [

### One-hot Encoding

In [174]:
from tensorflow.keras.utils import to_categorical

In [181]:
encoded = tokenizer.texts_to_sequences( results )[ 0 ]
ont_hot = to_categorical(encoded )
print( encoded )

[1]
